In [1]:
import json
import ast
from langchain_community.document_loaders import JSONLoader
from langchain_core.documents import Document
from langchain_naver import ChatClovaX, ClovaXEmbeddings
from langchain_chroma import Chroma
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnableParallel, RunnablePassthrough
from langchain_core.output_parsers import StrOutputParser

In [2]:
loader = JSONLoader(
    file_path="../data/data.json",
    jq_schema=".[]",
    text_content=False
)

raw_docs = loader.load()  

for doc in raw_docs:
    content_dict = json.loads(doc.page_content)
    doc.page_content = json.dumps(content_dict, ensure_ascii=False, indent=2)

In [3]:
raw_docs

[Document(metadata={'source': '/Users/9cheol2/Documents/project/data/data.json', 'seq_num': 1}, page_content='{\n  "site": "감사원",\n  "doc_code": "2551",\n  "sub_order": "00",\n  "category": "특정사안 | 공직기강 기타 | 기타",\n  "date": "2021.03.05",\n  "title": "토지주택연구원 관련 등 감사제보사항 점검",\n  "file_path": "https://kr.object.ncloudstorage.com/clabi-poc-storage/sr/bai/2551-00.pdf",\n  "download_url": "https://www.bai.go.kr/bai/result/branch/detail?srno=2551",\n  "contents": "감 사 원 문책 · 주의요구 및 통보 제 목 직무 관련 금품수수 및 연구과제 부당 수행 소 관 기 관 ① 한국토지주택공사 ② 국토교통과학기술진흥원 조 치 기 관 ① 한국토지주택공사 ② 국토교통과학기술진흥원 내 용 1. 사건 개요 한국토지주택공사 의 토지주택연구원 은 2014 년 9 월경 국토교통과학기술진흥원 에서 국 책연구과제로 추진한 ‘ 주거단지 내 유기성 폐자원의 활용촉진을 위한 실증연구 ’ 의 협동 연구 기관으로 지정되었고 , LH 연구원 ○ 실 연구위원 A 는 2014. 9. 21. 부터 2018. 12. 20. 까지 연구책임자로서 이 중 [ 그림 ] 과 같이 세부과제에 해당하는 ‘ 자족형 자원 순환 주거단지 실증연구 ’ 과제를 수행 하였다 . 그리고 A 는 국책과제 외에도 자원순환 단지 구현 등과 관련하여 LH 연 구원 자체 예산으로 추진한 ‘ 주택건축물에서 유기성 폐자원 재활용 시스템 구축연구 ’ 등 9 개 과제 를 2014 년 11 월부터 감사일 현재까지 연구책임자의 직책으로 수행하였거나 수행하고 있다 . 한편 국책과제 및 자체과제를 

In [4]:
def convert_docs(raw_docs):
    docs = []

    for d in raw_docs:
        s = d.page_content
        m = d.metadata

        if isinstance(s, str):
            s = ast.literal_eval(s)

        summary = s.get("contents_summary", {})
        
        if isinstance(summary, str):
            summary = ast.literal_eval(summary)

        text = (
            f"사례 제목: {summary.get('title_str', '')}\n"
            f"주요 키워드: {', '.join(summary.get('keyword_list', []))}\n\n"
            f"사례 개요:\n{summary.get('outline_str', '')}\n\n"
            f"문제점 상세:\n{summary.get('problems_str', '')}\n\n"
            f"관련 법령 및 기준:\n{summary.get('standards_str', '')}\n{summary.get('criteria_str', '')}\n\n"
            f"기관 판단 및 조치 내용:\n{summary.get('action_str', '')}\n"
        )

        meta = {
            "idx": m.get("seq_num"),
            "site": s.get("site"),
            "doc_code": s.get("doc_code"),
            "sub_order": s.get("sub_order"),
            "category": s.get("category"),
            "date": s.get("date"),
        }

        docs.append(
            Document(
                page_content=text,  
                metadata=meta       
            )
        )

    return docs

docs = convert_docs(raw_docs)

In [5]:
docs[0]

Document(metadata={'idx': 1, 'site': '감사원', 'doc_code': '2551', 'sub_order': '00', 'category': '특정사안 | 공직기강 기타 | 기타', 'date': '2021.03.05'}, page_content='사례 제목: 직무 관련 금품수수 및 연구과제 부당 수행\n주요 키워드: 직무 관련 금품수수, 부당한 연구과제 수행, 수의계약, 금품 수수, 허위 계약, 고가 구매, 분할 발주\n\n사례 개요:\n조치 기관: 한국토지주택공사, 국토교통과학기술진흥원 \n내 용: 세부과제의 부당한 진행과 금품수수 문제가 확인됨\n\n문제점 상세:\n연구책임자 A는 소액 수의계약을 통한 부당 계약 체결하며 허위계약, 고가의 물품 구입 등의 문제점을 보임. \nA는 85백만 원 이상의 연구개발비를 낭비하고 194백만 원 상당의 금품을 수수. \n연구 책임자 A의 관리와 감독 미흡으로 인한 부정행위 발생.\n\n관련 법령 및 기준:\n국가를 당사자로 하는 계약에 관한 법률 시행령 제 26조 제 1항 제 5호 \n임직원 행동강령 제 2조, 제 18조, 제 21조 \n과학기술기본법 제 11조의 2 제 1항 제 5호 및 제 7항\nLH 공사와 국토교통연구개발과 관련하여 엄격한 관리 및 감독 기준 마련 필요\n\n기관 판단 및 조치 내용:\n한국토지주택공사는 A에 대한 중징계 및 손실보전 방안 마련. 연구개발비 사용에 대한 철저한 계약관리 필요. \n국토교통과학기술진흥원은 정부출연금의 환수와 해당 책임자에 대한 제재 방안을 마련해야 함.\n')

In [6]:
print(docs[0].page_content)

사례 제목: 직무 관련 금품수수 및 연구과제 부당 수행
주요 키워드: 직무 관련 금품수수, 부당한 연구과제 수행, 수의계약, 금품 수수, 허위 계약, 고가 구매, 분할 발주

사례 개요:
조치 기관: 한국토지주택공사, 국토교통과학기술진흥원 
내 용: 세부과제의 부당한 진행과 금품수수 문제가 확인됨

문제점 상세:
연구책임자 A는 소액 수의계약을 통한 부당 계약 체결하며 허위계약, 고가의 물품 구입 등의 문제점을 보임. 
A는 85백만 원 이상의 연구개발비를 낭비하고 194백만 원 상당의 금품을 수수. 
연구 책임자 A의 관리와 감독 미흡으로 인한 부정행위 발생.

관련 법령 및 기준:
국가를 당사자로 하는 계약에 관한 법률 시행령 제 26조 제 1항 제 5호 
임직원 행동강령 제 2조, 제 18조, 제 21조 
과학기술기본법 제 11조의 2 제 1항 제 5호 및 제 7항
LH 공사와 국토교통연구개발과 관련하여 엄격한 관리 및 감독 기준 마련 필요

기관 판단 및 조치 내용:
한국토지주택공사는 A에 대한 중징계 및 손실보전 방안 마련. 연구개발비 사용에 대한 철저한 계약관리 필요. 
국토교통과학기술진흥원은 정부출연금의 환수와 해당 책임자에 대한 제재 방안을 마련해야 함.



In [ ]:
llm = ChatClovaX(
    model="HCX-DASH-002", 
    max_tokens=1024,
    api_key="your-api-key"
)

embeddings = ClovaXEmbeddings(
    model="bge-m3",
    api_key="your-api-key"
)

In [8]:
docs[0]

Document(metadata={'idx': 1, 'site': '감사원', 'doc_code': '2551', 'sub_order': '00', 'category': '특정사안 | 공직기강 기타 | 기타', 'date': '2021.03.05'}, page_content='사례 제목: 직무 관련 금품수수 및 연구과제 부당 수행\n주요 키워드: 직무 관련 금품수수, 부당한 연구과제 수행, 수의계약, 금품 수수, 허위 계약, 고가 구매, 분할 발주\n\n사례 개요:\n조치 기관: 한국토지주택공사, 국토교통과학기술진흥원 \n내 용: 세부과제의 부당한 진행과 금품수수 문제가 확인됨\n\n문제점 상세:\n연구책임자 A는 소액 수의계약을 통한 부당 계약 체결하며 허위계약, 고가의 물품 구입 등의 문제점을 보임. \nA는 85백만 원 이상의 연구개발비를 낭비하고 194백만 원 상당의 금품을 수수. \n연구 책임자 A의 관리와 감독 미흡으로 인한 부정행위 발생.\n\n관련 법령 및 기준:\n국가를 당사자로 하는 계약에 관한 법률 시행령 제 26조 제 1항 제 5호 \n임직원 행동강령 제 2조, 제 18조, 제 21조 \n과학기술기본법 제 11조의 2 제 1항 제 5호 및 제 7항\nLH 공사와 국토교통연구개발과 관련하여 엄격한 관리 및 감독 기준 마련 필요\n\n기관 판단 및 조치 내용:\n한국토지주택공사는 A에 대한 중징계 및 손실보전 방안 마련. 연구개발비 사용에 대한 철저한 계약관리 필요. \n국토교통과학기술진흥원은 정부출연금의 환수와 해당 책임자에 대한 제재 방안을 마련해야 함.\n')

In [9]:
docs[100]

Document(metadata={'idx': 101, 'site': '감사원', 'doc_code': '2631', 'sub_order': '00', 'category': '특정사안 | 공직기강 기타 | 공직기강', 'date': '2021.08.26'}, page_content="사례 제목: 민원서비스 종합평가 우수기관 포상 업무 처리 부적정\n주요 키워드: 민원서비스 종합평가, 부정행위, 병무청, 셀프민원, 표창 취소, 포상금 환수\n\n사례 개요:\n행정안전부와 국민권익위원회는 매년 민원서비스 종합평가를 실시하여 결과를 공개하고 관련 업무를 총괄한다. 평가 계획에는 자료 조작 등의 부정행위 시 감점, 우수사례로 선정 시 가점 부여가 포함되어 있다.\n\n문제점 상세:\n병무청은 2017~2019년 민원서비스 평가에서 '셀프민원'을 통해 점수를 부풀리는 부정행위를 하였다. 행안부는 이 사실을 모르고 병무청을 최우수기관으로 평가하여, 병무청은 2018년 대통령 표창과 포상금을 받았다.\n\n관련 법령 및 기준:\n민원서비스 종합평가 계획에 따르면 평가 관련 부정행위 발생 시 감점이 부여되며, 우수사례 포상 실적은 가점을 받는다. 상훈법 및 정부 표창 규정에 따라 서훈 공적이 거짓인 경우 표창 취소 및 부상을 환수할 수 있다.\n위반의 성격과 정보 조작 정도를 고려해야 하며, 평가 결과 왜곡을 방지하기 위한 추가적 예방조치가 필요하다.\n\n기관 판단 및 조치 내용:\n행정안전부장관은 병무청의 2018년도 민원서비스 종합평가 우수기관 표창과 포상금을 취소 및 환수하는 방안을 마련해야 한다.\n")

In [10]:
print(docs[0].page_content)

사례 제목: 직무 관련 금품수수 및 연구과제 부당 수행
주요 키워드: 직무 관련 금품수수, 부당한 연구과제 수행, 수의계약, 금품 수수, 허위 계약, 고가 구매, 분할 발주

사례 개요:
조치 기관: 한국토지주택공사, 국토교통과학기술진흥원 
내 용: 세부과제의 부당한 진행과 금품수수 문제가 확인됨

문제점 상세:
연구책임자 A는 소액 수의계약을 통한 부당 계약 체결하며 허위계약, 고가의 물품 구입 등의 문제점을 보임. 
A는 85백만 원 이상의 연구개발비를 낭비하고 194백만 원 상당의 금품을 수수. 
연구 책임자 A의 관리와 감독 미흡으로 인한 부정행위 발생.

관련 법령 및 기준:
국가를 당사자로 하는 계약에 관한 법률 시행령 제 26조 제 1항 제 5호 
임직원 행동강령 제 2조, 제 18조, 제 21조 
과학기술기본법 제 11조의 2 제 1항 제 5호 및 제 7항
LH 공사와 국토교통연구개발과 관련하여 엄격한 관리 및 감독 기준 마련 필요

기관 판단 및 조치 내용:
한국토지주택공사는 A에 대한 중징계 및 손실보전 방안 마련. 연구개발비 사용에 대한 철저한 계약관리 필요. 
국토교통과학기술진흥원은 정부출연금의 환수와 해당 책임자에 대한 제재 방안을 마련해야 함.



In [11]:
print(docs[1].page_content)

사례 제목: 법령 위반 규정 운영 및 부정당업자 입찰제한 업무 부당 처리
주요 키워드: 법령 위반, 부정당업자 등록, 입찰제한, 자체 규정, 징계처분, 감사 방해

사례 개요:
없음

문제점 상세:
▪ 법령에 위반된 규정을 임의로 제정 및 운영하여 부정당업자 입찰참가자격 제한 업무 처리

▪ 내부 규정을 변경 시 기획재정부장관 승인을 받지 않아 효력이 없음에도 운영됨

▪ 관련자들의 허위자료 제출 및 감사 방해 행위

관련 법령 및 기준:
공공기관의 운영에 관한 법률, 공기업·준정부기관 계약사무규칙, 국가를 당사자로 하는 계약에 관한 법률, 감사원법
폭로된 법령 위반 행위와 관련하여 징계처분을 위한 기준이 존재

기관 판단 및 조치 내용:
산업통상자원부장관은 관련자의 비위내용을 통보하고, 한국가스안전공사는 징계처분 및 자체 규정 제정 및 운영의 엄격한 관리 필요성을 촉구



In [12]:
# vector_store = Chroma(
#     embedding_function=embeddings,
#     persist_directory="../vector_db"
# )


In [13]:
# batch_size = 100  

# for i in range(0, len(docs), batch_size):
#     batch = docs[i:i+batch_size]
#     vector_store.add_documents(batch)
#     print(f"{i+len(batch)} / {len(docs)} inserted")

In [14]:
vector_store = Chroma(
    embedding_function=embeddings,
    persist_directory="../vector_db"
)

In [15]:
retriever = vector_store.as_retriever(
    search_type="similarity",
    search_kwargs={"k": 3}
)

In [16]:
input = "수의계약 감사에 참고할 만한 문서를 알려줘."

In [17]:
topk_docs = retriever.invoke(input)
print(topk_docs)

[Document(id='223130f2-b901-4f84-81b5-b79d92866a6a', metadata={'site': 'ALIO 공공기관 경영정보 공개시스템', 'idx': 632, 'doc_code': '2022070802463316', 'date': '2022.07.07', 'sub_order': '15', 'category': '인천국제공항공사 | C0105'}, page_content='사례 제목: 수의계약 근거 및 검토 미비\n주요 키워드: 수의계약, 국가계약법, 경쟁의편익, 계약사유서, 계약관리절차\n\n사례 개요:\n○○○(주)는 국가계약법에 의해 수의계약의 사유를 명시하고 있으며, 회사 내부 규정에서도 이를 따르고 있음. 감사결과, 수의계약 총 49건 중 1천만원 이상의 수의계약에서 사유서를 작성하지 않거나 절차를 무시한 사례가 발견됨. 특히, 일부 계약은 1회 유찰 후 바로 수의계약으로 전환되어 논란이 됨.\n\n문제점 상세:\n계약사유서를 작성하지 않은 사례 3건\n경쟁의 편익이 없다는 이유로 1회 유찰 후 수의계약으로 전환한 사례 2건\n계약부서의 사전 협조결재 없이 사후 통보한 사례 3건\n\n관련 법령 및 기준:\n수의계약의 근거 및 절차는 국가계약법 시행령 제26조 및 제27조에 의해 규정됨. 회사는 계약 관리 절차서에서 해당 법령의 수의계약 사유를 충족할 경우에 제한적으로 적용하도록 강조.\n없음\n\n기관 판단 및 조치 내용:\n수의계약 추진 시 국가계약법에 명시된 수의계약 근거를 철저히 검토\n수의계약 사유서 작성 및 계약부서의 사전 검토 철저 이행\n'), Document(id='94916372-b662-423f-b54b-2b57a3dc746e', metadata={'doc_code': '2022021102382109', 'sub_order': '00', 'site': 'ALIO 공공기관 경영정보 공개시스템', 'category': '한국토지주택공사 | C0396', 'date': '2022.02.10', 'idx': 

In [18]:
system_prompt = """
너는 공공기관 감사보고서 기반 RAG 어시스턴트이다.

반드시 아래 원칙을 준수하라:

1. 너의 모든 답변은 RAG가 제공한 문서(context)에 근거해야 한다.
2. 문서에 명시되지 않은 내용은 절대로 추론하거나 상상하지 않는다.
3. 문서에 근거가 없으면 "제공된 문서만으로는 답변할 수 없습니다."라고 답한다.
4. 문서에 포함된 사실, 수치, 기관명, 조치 내용 등은 있는 그대로 전달한다.
5. 내용을 요약·정리할 수는 있지만 새로운 사실을 생성해서는 안 된다.
6. 문서를 인용할 때는 자연스럽게 문장 안에서 재서술한다.
7. 여러 문서를 제공받으면 서로 모순되는지 먼저 확인하고, 모순될 경우 문서별로 구분해 설명한다.
8. 감사 업무 특성상, 문서의 “기관 판단 및 조치 내용”을 최우선적으로 반영한다.
9. 질문이 모호하면 문서 범위 내에서 가장 명확한 답을 제공하되, 문서 외 해석은 하지 않는다.

너의 목표는 사용자가 문서를 정확히 이해할 수 있도록,
문서 내용을 기반으로만 정확하고 신뢰 가능한 해석을 제공하는 것이다.
"""

template = ChatPromptTemplate.from_messages([
    ("system", system_prompt),
    ("human", "{context}\n\ninput: {input}")
])

In [19]:
rag_chain = (
    RunnableParallel({
        "context": lambda x: "\n\n".join([d.page_content for d in retriever.invoke(x["input"])]),
        "input": RunnablePassthrough()
    })
    | template
    | llm
    | StrOutputParser()
)

In [20]:
output = rag_chain.invoke({"input": input})
print(input)
print(output)

수의계약 감사에 참고할 만한 문서를 알려줘.
감사 시 수의계약 관련 감사에 참고할 만한 문서는 다음과 같습니다.

1. **수의계약업무지침**: 수의계약의 근거 및 절차가 명시되어 있습니다.
2. **견적가격업무처리지침**: 200만 원을 초과하는 용역의 경우 두 개 이상의 업체에 견적을 요청해야 한다는 등의 내용이 포함되어 있습니다.
3. **국가계약법 시행령 제26조 및 제27조**: 수의계약의 근거 및 절차에 대한 규정이 담겨 있습니다.
4. **계약 관리 절차서**: 회사가 내부 규정에서 따르는 계약 관리 절차서가 포함됩니다.

이러한 문서들은 수의계약의 근거, 절차, 그리고 그에 따른 관리 절차를 이해하는 데 도움이 될 것입니다.
